In [ ]:
#!pip3 install matplotlib PyQt5
#!pip3 install rasterio geopandas matplotlib

!python -m pip install matplotlib PyQt5
!python -m pip install rasterio geopandas matplotlib

In [3]:
import rasterio
from rasterio.plot import show
import geopandas as gpd
import matplotlib.pyplot as plt
from shapely.geometry import Point

# File paths
tif_file_path = '/Users/taekim/ecohackathon/WeCanopy/test/TreeCrownVectorDataset_761588_9673769_20_20_32720.tif'
geojson_file_path = '/Users/taekim/ecohackathon/WeCanopy/test/result.geojson'

# Read the TIF file
with rasterio.open(tif_file_path) as src:
    tif_image = src.read([1, 2, 3])  # Read the first three bands (RGB)
    tif_transform = src.transform

# Read the GeoJSON file
geojson_data = gpd.read_file(geojson_file_path)

# Set the interactive backend to Qt5Agg
plt.switch_backend('Qt5Agg') # You have to install PyQt5

# Enable interactive mode
plt.ion()

# Plotting
fig, ax = plt.subplots(figsize=(10, 10))

# Plot the RGB TIF image
show(tif_image, transform=tif_transform, ax=ax)

# Plot the GeoJSON polygons
geojson_data.plot(ax=ax, facecolor='none', edgecolor='red')

# Set plot title
ax.set_title('TIF Image with Tree Crowns Overlay')

# Create an annotation box
annot = ax.annotate("", xy=(0, 0), xytext=(20, 20),
                    textcoords="offset points",
                    bbox=dict(boxstyle="round", fc="w"),
                    arrowprops=dict(arrowstyle="->"))
annot.set_visible(False)

# Create a function to handle mouse clicks
def on_click(event):
    if event.inaxes is not None:
        # Get the coordinates of the click
        click_point = Point(event.xdata, event.ydata)
        # Check if the click is within any of the polygons
        for idx, row in geojson_data.iterrows():
            if row['geometry'].contains(click_point):
                # Access the properties dictionarㅋ
                # Extract species and confidence score
                species_info = row['species']
                confidence_score = row['Confidence_score']
                # Display information about the clicked polygon
                annot.xy = (event.xdata, event.ydata)
                text = f"Polygon {idx}\n\nConfidence:\n{confidence_score}\n\nSpecies and their probability:\n{species_info}"
                annot.set_text(text)
                annot.set_visible(True)
                fig.canvas.draw()
                break
# Connect the click event to the handler function
cid = fig.canvas.mpl_connect('button_press_event', on_click)

# Show plot
plt.show()

# Keep the plot open
plt.ioff()
plt.show()

id                                                               df_1
Confidence_score                                              0.61348
species             [ [ "Myrcia", 0.44138795137405396 ], [ "Ocotea...
geometry            POLYGON ((761574.1236583593 9673794.9223366, 7...
Name: 1, dtype: object
1
